# Řešení 1. série

In [1]:
from manim import *

## Míchání

In [2]:
%%manim -v WARNING -qh Shuffle

from random import *


class Shuffle(Scene):
    def construct(self):
        seed(0xdeadbeef)
        
        # počet hodnot k míchání
        n = 5

        circles = [
            Circle(color=WHITE, fill_opacity=0.8, fill_color=WHITE).scale(0.6)
            for _ in range(n)
        ]

        # mezery mezi kruhy
        spacing = 2
        for i, circle in enumerate(circles):
            circle.shift(RIGHT * (i - (len(circles) - 1) / 2) * spacing)

        self.play(*[Write(circle) for circle in circles])

        # vybraný kruh
        selected = randint(0, n - 1)
        self.play(circles[selected].animate.set_color(RED))
        self.play(circles[selected].animate.set_color(WHITE))

        # postupné zrychlování při navazujících prohozeních
        swaps = 13
        speed_start = 1
        speed_end = 0.2

        for i in range(swaps):
            speed = speed_start - abs(speed_start - speed_end) / swaps * i
            
            # vybrání dvou různých náhodných kruhů
            a, b = sample(range(n), 2)
            
            # prohození s o trochu větším úhlem, jinak přes sebe kruhy procházejí, což není hezké
            self.play(
                Swap(circles[a], circles[b]), run_time=speed, path_arc=135 * DEGREES
            )

        # zvýraznění původních kruhů
        self.play(circles[selected].animate.set_color(RED))
        self.play(circles[selected].animate.set_color(WHITE))

## Třízení

In [3]:
%%manim -v WARNING -qh Sort

from random import *


class Sort(Scene):
    def construct(self):
        seed(0xdeadbeef)
        
        # počet hodnot ke třízení
        n = 20

        # nejmenší a největší hodnta
        value_min, value_max = 1, 20

        # hodnoty v poli
        values = [randint(value_min, value_max) for _ in range(n)]

        # šířka čtverce a výška jedné hodnoty (tzn. číslo 5 má výšku 5 * unit_height)
        rectangle_width = 0.2
        unit_height = 0.2

        # mezera mezi obdélníky
        rectangle_spacing = 2.5
        
        rectangles = [
            Rectangle(
                width=rectangle_width,
                height=unit_height * v,
                fill_color=WHITE,
                fill_opacity=1,
            )
            for v in values
        ]
        
        # bod, podle kterého budeme rovnat spodek přes funkci align_to
        # aby byly čtverce vycentrované, bude odpovídat spodku nejvyšší hodnoty
        alignment_point = None
        max_value = 0
        for i, v in enumerate(values):
            if max_value < v:
                max_value = v
                alignment_point = Point().shift(DOWN * rectangles[i].height / 2)

        # posun obdélníků tak, aby byly rovnoměrně rozprostřené a zarovnané dolů
        for i, rect in enumerate(rectangles):
            rect.shift(
                RIGHT
                * (i - (len(rectangles) - 1) / 2)
                * rectangle_width
                * rectangle_spacing
            ).align_to(alignment_point, DOWN)

        self.play(*[Write(r) for r in rectangles])

        def animate_at(a, b, duration):
            """Animace toho, že se aktuálně díváme na pozice a a b."""
            self.play(
                *[
                    r.animate.set_color(WHITE if i not in (a, b) else YELLOW)
                    for i, r in enumerate(rectangles)
                ],
                run_time=duration,
            )

        def animate_swap(a, b, duration):
            """Animace prohození a a b (s tím, že v poli values už jsou prohozené)."""
            self.play(
                # jelikož stretch_to_fit_height stretchuje z prostředku, musíme alignnout na bod
                rectangles[a]
                .animate.stretch_to_fit_height(values[a] * unit_height)
                .align_to(alignment_point, DOWN),
                rectangles[b]
                .animate.stretch_to_fit_height(values[b] * unit_height)
                .align_to(alignment_point, DOWN),
                run_time=duration,
            )

        # při prvním průchodu jsou animace pomalejší
        speed_slow = 0.6
        speed_fast = 0.07

        for i in range(n):
            speed = speed_slow if i == 0 else speed_fast
            swapped = False
            for j in range(n - i - 1):
                animate_at(j, j + 1, speed)

                if values[j] > values[j + 1]:
                    values[j], values[j + 1] = values[j + 1], values[j]

                    animate_swap(j, j + 1, speed)
                    swapped = True

            # pokud jsme při průchodu nic neprohodili, tak už není co třídit
            if not swapped:
                break

        self.play(*[FadeOut(r) for r in rectangles])

## Vyhledávání

In [4]:
%%manim -v WARNING -qh Search

from random import *


class Search(Scene):
    def construct(self):
        seed(0xdeadbeef4)  # hezčí vstup :)
        
        # počet hodnot ke třízení
        n = 10

        # nejmenší a největší hodnta
        value_min, value_max = 1, n

        # hodnoty v poli
        values = sorted([randint(value_min, value_max) for _ in range(n)])

        square_side_length = 0.75
        square_spacing = 1.3

        squares = [Square(side_length=square_side_length) for v in values]
        numbers = [Tex(f"${v}$") for v in values]

        # posun čtverců tak, aby byly uprostřed obrazovky
        for i, rect in enumerate(squares):
            rect.shift(
                RIGHT
                * (i - (len(squares) - 1) / 2)
                * square_side_length
                * square_spacing
            )

        # posun textu tak, aby byly uvnitř čtverců
        for i, number in enumerate(numbers):
            number.move_to(squares[i])

        # pointery na to, kde aktuálně jsme
        pointer_length = 0.4
        l_arrow = Arrow(start=DOWN * pointer_length, end=UP).next_to(squares[0], DOWN)
        r_arrow = Arrow(start=DOWN * pointer_length, end=UP).next_to(squares[-1], DOWN)

        self.play(*[Write(s) for s in squares], *[Write(n) for n in numbers])

        # vypsání čísla, které hledáme
        target = randint(value_min, value_max)
        text = Tex(f"Hledáme: ${target}$").shift(UP * 1.5)

        self.play(Write(text))

        self.play(Write(l_arrow), Write(r_arrow))

        lo, hi = 0, len(values) - 1

        def color_in_range(objects, color, range):
            """Vrátí seznam animací vybarvení daných objektů v daném rozmezí."""
            return [
                o.animate.set_color(color) for i, o in enumerate(objects) if i in range
            ]

        # samotný algoritmus
        while lo < hi:
            avg = (lo + hi) // 2
            
            # vykreslení pointeru u aktuálního prvku
            current_arrow = Arrow(start=DOWN * pointer_length, end=UP) \
                .next_to(squares[avg], DOWN) \
                .set_color(ORANGE)
            
            self.play(Write(current_arrow))

            if values[avg] < target:
                # posunutí levého pointeru
                self.play(
                    FadeOut(current_arrow),
                    l_arrow.animate.next_to(squares[avg + 1], DOWN),
                    *color_in_range(squares, DARK_GRAY, range(lo, avg + 1)),
                    *color_in_range(numbers, DARK_GRAY, range(lo, avg + 1)),
                )

                lo = avg + 1
            elif values[avg] >= target:
                # posunutí pravého pointeru
                self.play(
                    FadeOut(current_arrow),
                    r_arrow.animate.next_to(squares[avg], DOWN),
                    *color_in_range(squares, DARK_GRAY, range(avg + 1, hi + 1)),
                    *color_in_range(numbers, DARK_GRAY, range(avg + 1, hi + 1)),
                )

                hi = avg

            # nalezení hledané hodnoty
            if values[hi] == target:
                self.play(
                    *color_in_range(squares, DARK_GRAY, range(hi)),
                    *color_in_range(squares, DARK_GRAY, range(hi+1, n)),
                    *color_in_range(numbers, DARK_GRAY, range(hi)),
                    *color_in_range(numbers, DARK_GRAY, range(hi+1, n)),
                    numbers[hi].animate.set_color(GREEN),
                    squares[hi].animate.set_color(GREEN),
                    FadeOut(l_arrow),
                )
                break
        
        
        self.play(*[FadeOut(r) for r in numbers + squares + [r_arrow, text]])